In [41]:
#importação das bibliotecas
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import make_column_transformer

In [11]:
# Carregamento dos dados para análise da extrutura
base_tratada_caminho = '..\\Base de dados\\Base_tratada.csv'

# Leitura dos arquivos CSV de acidentes e empreendimentos
base_tratada_df = pd.read_csv(base_tratada_caminho)
pd.set_option('display.max_columns', None)
base_tratada_df

C:\Users\kaiog\AppData\Local\Temp\ipykernel_34508\718623421.py:5: DtypeWarning: Columns (43,63) have mixed types. Specify dtype option on import or set low_memory=False.
  base_tratada_df = pd.read_csv(base_tratada_caminho)


Unnamed: 0    cod_mdr  cod_operacao  cod_saci  cod_convenio_siafi  \
0                0    1-38001      319910.0   38001.0                 0.0   
1                1    1-38001      319910.0   38001.0                 0.0   
2                2    1-38001      319910.0   38001.0                 0.0   
3                3    1-38001      319910.0   38001.0                 0.0   
4                4    1-38001      319910.0   38001.0                 0.0   
...            ...        ...           ...       ...                 ...   
376749      376749  2-0402954      402954.0       NaN                 0.0   
376750      376750  2-0402954      402954.0       NaN                 0.0   
376751      376751  2-0402954      402954.0       NaN                 0.0   
376752      376752  2-0402954      402954.0       NaN                 0.0   
376753      376753  2-0402954      402954.0       NaN                 0.0   

        cod_ag_operador           origem          dsc_concedente dsc_fonte  \
0              375658.0         PAC_MCID  MINISTERIO DAS CIDADES       FIN   
1              375658.0         PAC_MCID  MINISTERIO DAS CIDADES       FIN   
2              375658.0         PAC_MCID  MINISTERIO DAS CIDADES       FIN   
3              375658.0         PAC_MCID  MINISTERIO DAS CIDADES       FIN   
4              375658.0         PAC_MCID  MINISTERIO DAS CIDADES       FIN   
...                 ...              ...                     ...       ...   
376749              NaN  NPAC_DBGESTORES  MINISTERIO DAS CIDADES       OGU   
376750              NaN  NPAC_DBGESTORES  MINISTERIO DAS CIDADES       OGU   
376751              NaN  NPAC_DBGESTORES  MINISTERIO DAS CIDADES       OGU   
376752              NaN  NPAC_DBGESTORES  MINISTERIO DAS CIDADES       OGU   
376753              NaN  NPAC_DBGESTORES  MINISTERIO DAS CIDADES       OGU   

       dsc_unidade cod_proposta dsc_situacao_contrato_mdr bln_carteira_mdr  \
0            SEMOB          NaN    CONTRATADO - CONCLUIDO              SIM   
1            SEMOB          NaN    CONTRATADO - CONCLUIDO              SIM   
2            SEMOB          NaN    CONTRATADO - CONCLUIDO              SIM   
3            SEMOB          NaN    CONTRATADO - CONCLUIDO              SIM   
4            SEMOB          NaN    CONTRATADO - CONCLUIDO              SIM   
...            ...          ...                       ...              ...   
376749       SEMOB          NaN   CANCELADO OU DISTRATADO              NAO   
376750       SEMOB          NaN   CANCELADO OU DISTRATADO              NAO   
376751       SEMOB          NaN   CANCELADO OU DISTRATADO              NAO   
376752       SEMOB          NaN   CANCELADO OU DISTRATADO              NAO   
376753       SEMOB          NaN   CANCELADO OU DISTRATADO              NAO   

       bln_carteira_mdr_ativo dsc_situacao_objeto_mdr dsc_paralisada_mdr  \
0                         NAO               CONCLUIDA     NAO PARALISADA   
1                         NAO               CONCLUIDA     NAO PARALISADA   
2                         NAO               CONCLUIDA     NAO PARALISADA   
3                         NAO               CONCLUIDA     NAO PARALISADA   
4                         NAO               CONCLUIDA     NAO PARALISADA   
...                       ...                     ...                ...   
376749                    NAO            NAO INICIADA     NAO PARALISADA   
376750                    NAO            NAO INICIADA     NAO PARALISADA   
376751                    NAO            NAO INICIADA     NAO PARALISADA   
376752                    NAO            NAO INICIADA     NAO PARALISADA   
376753                    NAO            NAO INICIADA     NAO PARALISADA   

       bln_ativo bln_ativo_boolean  cod_id_fonte   cod_id_pac programa  acao  \
0              S                 Y        375658        38001  PAC FIN  FGTS   
1              S                 Y        375658        38001  PAC FIN  FGTS   
2              S                 Y        375658        

# Ajuste dos dados para correlação de pearson

In [35]:
# Filtrar colunas relevantes
colunas_relevantes = ['origem', 'dsc_fonte', 'dsc_unidade', 'dsc_situacao_contrato_mdr','uf_SIGLA_UF_x','mun_MUNNOMEX_x',
'vlr_repasse_financiamento','vlr_contrapartida','vlr_desembolsado','vlr_desbloqueado','situacao_obra','vlr_ult_desembolso',
'vlr_ult_repasse_desbloqueado','vlr_ult_contrapartida_desbloqueado','dias_paralisados','emp_gerado','vlr_investimento','vlr_repasse_financiamento_num',
'vlr_contrapartida_num','vlr_investimento_num','vlr_empenhado_num','vlr_desbloqueado_num','Populacao_x','mun_AREA_x','Categoria_emprendimentos',
'Pedestre_mortes','Ciclista_mortes','Motociclista_mortes','Ocup_triciclo_motor_mortes','Ocup_automovel_mortes','Ocup_caminhonete_mortes','Ocup_veic_transp_pesado_mortes',
'Ocup_onibus_mortes','Outros_mortes','total_mortes','taxa_mun_mortes','taxa_mun_pedestre_mortes','taxa_mun_ciclista_mortes','taxa_mun_motociclista_mortes',
'taxa_mun_automovel_mortes','taxa_mun_veiculo_pesado_mortes','taxa_mun_onibus_mortes','taxa_mun_outros_mortes','Pedestre_feridos','Ciclista_feridos','Motociclista_feridos',
'Ocup_triciclo_motor_feridos','Ocup_automovel_feridos','Ocup_caminhonete_feridos','Ocup_veic_transp_pesado_feridos','Ocup_onibus_feridos','Outros_feridos','total_feridos',
'taxa_mun_feridos','taxa_mun_pedestre_feridos','taxa_mun_ciclista_feridos','taxa_mun_motociclista_feridos','taxa_mun_automovel_feridos','taxa_mun_veiculo_pesado_feridos',
'taxa_mun_onibus_feridos','taxa_mun_outros_feridos']

# Filtrar o DataFrame para manter apenas as colunas relevantes
df_filtrado = base_tratada_df[colunas_relevantes]
df_filtrado.dropna()
df_filtrado['vlr_desembolsado'].fillna(df_filtrado['vlr_desembolsado'].mean(), inplace=True)
df_filtrado['vlr_desbloqueado'].fillna(df_filtrado['vlr_desbloqueado'].mean(), inplace=True)
df_filtrado['vlr_ult_desembolso'].fillna(df_filtrado['vlr_ult_desembolso'].mean(), inplace=True)
df_filtrado['vlr_ult_repasse_desbloqueado'].fillna(df_filtrado['vlr_ult_repasse_desbloqueado'].mean(), inplace=True)
df_filtrado['dias_paralisados'].fillna(df_filtrado['dias_paralisados'].mean(), inplace=True)
df_filtrado['Populacao_x'].fillna(df_filtrado['Populacao_x'].mean(), inplace=True)
df_filtrado['mun_AREA_x'].fillna(df_filtrado['mun_AREA_x'].mean(), inplace=True)
df_filtrado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 376754 entries, 0 to 376753
Data columns (total 61 columns):
 #   Column                              Non-Null Count   Dtype  
---  ------                              --------------   -----  
 0   origem                              376754 non-null  object 
 1   dsc_fonte                           376754 non-null  object 
 2   dsc_unidade                         376754 non-null  object 
 3   dsc_situacao_contrato_mdr           376754 non-null  object 
 4   uf_SIGLA_UF_x                       376754 non-null  object 
 5   mun_MUNNOMEX_x                      375154 non-null  object 
 6   vlr_repasse_financiamento           376754 non-null  float64
 7   vlr_contrapartida                   376754 non-null  float64
 8   vlr_desembolsado                    376754 non-null  float64
 9   vlr_desbloqueado                    376754 non-null  float64
 10  situacao_obra                       376704 non-null  object 
 11  vlr_ult_desembolso        

C:\Users\kaiog\AppData\Local\Temp\ipykernel_34508\1679973764.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_filtrado['vlr_desembolsado'].fillna(df_filtrado['vlr_desembolsado'].mean(), inplace=True)
C:\Users\kaiog\AppData\Local\Temp\ipykernel_34508\1679973764.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_filtrado['vlr_desbloqueado'].fillna(df_filtrado['vlr_desbloqueado'].mean(), inplace=True)
C:\Users\kaiog\AppData\Local\Temp\ipykernel_34508\1679973764.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas

- Variáveis dummy, também conhecidas como variáveis indicadoras, são ferramentas usadas em análises estatísticas para representar categorias ou atributos qualitativos de forma numérica. 
- Modo de uso:
    - Transformação: Cada categoria da variável original é transformada em uma nova variável binária (0 ou 1). 
    - Codificação: Cada variável dummy terá o valor 1 se a observação pertencer àquela categoria, e 0 caso contrário.
    - Interpretação no Modelo: Incluir essas variáveis dummy em um modelo de regressão permite estimar o efeito de cada categoria, mantendo as outras variáveis no modelo controladas.

In [44]:
# Codificar todas as colunas categóricas usando get_dummies
df_encoded = pd.get_dummies(df_filtrado, columns=['origem', 'dsc_fonte', 'dsc_unidade', 'dsc_situacao_contrato_mdr', 
                                                  'uf_SIGLA_UF_x', 'mun_MUNNOMEX_x', 'situacao_obra', 'Categoria_emprendimentos'])

In [45]:
df_encoded

vlr_repasse_financiamento  vlr_contrapartida  vlr_desembolsado  \
0                     62211677.65        15708716.86      6.221168e+07   
1                     62211677.65        15708716.86      6.221168e+07   
2                     62211677.65        15708716.86      6.221168e+07   
3                     62211677.65        15708716.86      6.221168e+07   
4                     62211677.65        15708716.86      6.221168e+07   
...                           ...                ...               ...   
376749                  245850.00            5000.00      1.171445e+06   
376750                  245850.00            5000.00      1.171445e+06   
376751                  245850.00            5000.00      1.171445e+06   
376752                  245850.00            5000.00      1.171445e+06   
376753                  245850.00            5000.00      1.171445e+06   

        vlr_desbloqueado  vlr_ult_desembolso  vlr_ult_repasse_desbloqueado  \
0           6.221168e+07       305872.530000                      0.000000   
1           6.221168e+07       305872.530000                      0.000000   
2           6.221168e+07       305872.530000                      0.000000   
3           6.221168e+07       305872.530000                      0.000000   
4           6.221168e+07       305872.530000                      0.000000   
...                  ...                 ...                           ...   
376749      1.214703e+06       176571.021747                  68804.702013   
376750      1.214703e+06       176571.021747                  68804.702013   
376751      1.214703e+06       176571.021747                  68804.702013   
376752      1.214703e+06       176571.021747                  68804.702013   
376753      1.214703e+06       176571.021747                  68804.702013   

        vlr_ult_contrapartida_desbloqueado  dias_paralisados  emp_gerado  \
0                                      0.0       1382.000000        1437   
1                                      0.0       1382.000000        1437   
2                                      0.0       1382.000000        1437   
3                                      0.0       1382.000000        1437   
4                                      0.0       1382.000000        1437   
...                                    ...               ...         ...   
376749                                 NaN       4671.910735           6   
376750                                 NaN       4671.910735           6   
376751                                 NaN       4671.910735           6   
376752                                 NaN       4671.910735           6   
376753                                 NaN       4671.910735           6   

        vlr_investimento  vlr_repasse_financiamento_num  \
0            77920394.51                     62200000.0   
1            77920394.51                     62200000.0   
2            77920394.51                     62200000.0   
3            77920394.51                     62200000.0   
4            77920394.51                     62200000.0   
...                  ...                            ...   
376749         250850.00                    245800000.0   
376750         250850.00                    245800000.0   
376751         250850.00                    245800000.0   
376752         250850.00                    245800000.0   
376753         250850.00                    245800000.0   

        vlr_contrapartida_num  vlr_investimento_num  vlr_empenhado_num  \
0                  15700000.0            77900000.0                0.0   
1                  15700000.0            77900000.0                0.0   
2                  15700000.0            77900000.0                0.0   
3                  15700000.0            77900000.0                0.0   
4                  15700000.0            77900000.0                0.0   
...                       ...                   ...                ...   
376749              5000000.0           25

In [47]:
#calculo da correlação para variável de interesse

# A variável alvo
variavel_alvo = 'total_mortes'

# Criar um DataFrame para armazenar as correlações
correlacoes = pd.Series(dtype=float)

# Calcular a correlação para cada coluna com a variável alvo
for coluna in df_encoded.columns:
    if coluna != variavel_alvo:  # Evitar a correlação da variável com ela mesma
        correlacao = np.corrcoef(df_encoded[variavel_alvo], df_encoded[coluna])[0, 1]
        correlacoes[coluna] = correlacao

In [55]:
# Selecionar os 10 maiores valores negativos e os 10 maiores valores positivos
maiores_positivos = correlacoes.sort_values(ascending=False).head(10)
maiores_negativos = correlacoes.sort_values(ascending=True).head(10)

# Exibir os resultados
print("Maiores correlações negativas:")
print(maiores_negativos)
print("\nMaiores correlações positivas:")
print(maiores_positivos)

Maiores correlações negativas:
origem_NPAC_DBGESTORES                                         -0.327282
dsc_unidade_SEMOB                                              -0.316256
dsc_fonte_OGU                                                  -0.229887
situacao_obra_OBJETO CONCLUÍDO                                 -0.116942
Categoria_emprendimentos_Pavimentação, Drenagem e Saneamento   -0.100818
dias_paralisados                                               -0.099279
dsc_situacao_contrato_mdr_CONTRATADO - CONCLUIDO               -0.060002
uf_SIGLA_UF_x_SC                                               -0.047730
uf_SIGLA_UF_x_RS                                               -0.044164
vlr_empenhado_num                                              -0.034794
dtype: float64

Maiores correlações positivas:
Pedestre_mortes           0.946139
Motociclista_mortes       0.937442
Ocup_automovel_mortes     0.870684
total_feridos             0.863166
Ciclista_mortes           0.834841
Pedestre_feridos 

- As variáveis acima são as que mais influenciam o número de mortes de acordo com a correlação
- Valores positivos e próximos de 1, indicam alta correlação positivia, indicando que quando estes valores são maiores, maiores são os número de mortes, como exemplo a ocupação de automóveis envolvidos em acidentes com mortes com correlação de 0,87
- Valores negativos e próximos de -1, indicam alta correlação negativa, indicando que quanto maiores, menores são os valores total de mortes. Um caso interessante é a situação da obra estar concluída, tendo impacto direto na redução do número de mortes
- Obras do tipo de pavimentação, drenagem e saneamento aparentam ter impacto direto na redução do número total de mortes

# modelagem supervisionada do total de mortes

In [56]:
# Selecionar variáveis relevantes para prever mortes totais
features = ['origem_NPAC_DBGESTORES', 'dsc_unidade_SEMOB', 'dsc_fonte_OGU', 'situacao_obra_OBJETO CONCLUÍDO',
            'Categoria_emprendimentos_Pavimentação, Drenagem e Saneamento','Pedestre_mortes','Motociclista_mortes',
           'Ocup_automovel_mortes','total_feridos']
target = 'total_mortes'

In [57]:
# Criar os conjuntos de treino e teste
X = df_encoded[features]
y = df_encoded[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [58]:
# Configurar e treinar o modelo de regressão linear
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

LinearRegression()

In [59]:
# Fazer previsões com o conjunto de teste
y_pred = linear_model.predict(X_test)

# Avaliar a performance do modelo
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("MSE:", mse, "R2:", r2)

MSE: 180.18172556150708 R2: 0.9700770132763181


In [62]:
from sklearn.ensemble import RandomForestRegressor

# Configurar e treinar o modelo Random Forest
random_forest_model = RandomForestRegressor(n_estimators=100, random_state=42)
random_forest_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred_rf = random_forest_model.predict(X_test)

# Avaliar a performance do modelo
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2_rf = r2_score(y_test, y_pred_rf)

# Retornar a importância das variáveis, MSE e R²
rf_feature_importances = random_forest_model.feature_importances_
print("MSE:", mse_rf, "\nR2: ", r2_rf, "\nFeatures Importance: ", rf_feature_importances)

MSE: 3.6292970967201295 
R2:  0.9993972784503922 
Features Importance:  [1.03515500e-05 2.50078601e-06 8.84242067e-06 2.52038407e-05
 2.34826523e-05 7.85413260e-01 1.91122907e-01 1.38019954e-02
 9.59145665e-03]


- Um modelo simples de regressão mmúltipla parece suprir a necessidade para prever variáveis de sisnistros, uma vez que as correlações são altas
- Porém um modelo ensable learning de floresta aleatória apresentou melhores com maior acurácia de previsão e erro quadrático médio menor

# Repetindo o processo para a variável de Pedestre_mortes

In [63]:
#calculo da correlação para variável de interesse

# A variável alvo
variavel_alvo = 'Pedestre_mortes'

# Criar um DataFrame para armazenar as correlações
correlacoes = pd.Series(dtype=float)

# Calcular a correlação para cada coluna com a variável alvo
for coluna in df_encoded.columns:
    if coluna != variavel_alvo:  # Evitar a correlação da variável com ela mesma
        correlacao = np.corrcoef(df_encoded[variavel_alvo], df_encoded[coluna])[0, 1]
        correlacoes[coluna] = correlacao
        

# Selecionar os 10 maiores valores negativos e os 10 maiores valores positivos
maiores_positivos = correlacoes.sort_values(ascending=False).head(10)
maiores_negativos = correlacoes.sort_values(ascending=True).head(10)

# Exibir os resultados
print("Maiores correlações negativas:")
print(maiores_negativos)
print("\nMaiores correlações positivas:")
print(maiores_positivos)

Maiores correlações negativas:
dsc_unidade_SEMOB                                              -0.339561
origem_NPAC_DBGESTORES                                         -0.297740
dsc_fonte_OGU                                                  -0.211973
situacao_obra_OBJETO CONCLUÍDO                                 -0.106748
Categoria_emprendimentos_Pavimentação, Drenagem e Saneamento   -0.091121
dias_paralisados                                               -0.089543
dsc_situacao_contrato_mdr_CONTRATADO - CONCLUIDO               -0.052461
vlr_empenhado_num                                              -0.045828
taxa_mun_automovel_mortes                                      -0.039365
uf_SIGLA_UF_x_SC                                               -0.039128
dtype: float64

Maiores correlações positivas:
total_mortes              0.946139
Motociclista_mortes       0.844175
Pedestre_feridos          0.826105
total_feridos             0.812776
Ocup_automovel_mortes     0.811130
Ciclista_mortes  

In [65]:
# Selecionar variáveis relevantes para prever mortes de pedestres
features = ['dsc_unidade_SEMOB', 'origem_NPAC_DBGESTORES','dsc_fonte_OGU','situacao_obra_OBJETO CONCLUÍDO',
            'Motociclista_mortes','Pedestre_feridos','total_feridos','Ocup_automovel_mortes']
target = 'Pedestre_mortes'

# Criar os conjuntos de treino e teste
X = df_encoded[features]
y = df_encoded[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [66]:
# Configurar e treinar o modelo de regressão linear
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred = linear_model.predict(X_test)

# Avaliar a performance do modelo
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("MSE:", mse, "R2:", r2)

MSE: 136.9452168537884 R2: 0.8466816319679896


In [67]:
from sklearn.ensemble import RandomForestRegressor

# Configurar e treinar o modelo Random Forest
random_forest_model = RandomForestRegressor(n_estimators=100, random_state=42)
random_forest_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred_rf = random_forest_model.predict(X_test)

# Avaliar a performance do modelo
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2_rf = r2_score(y_test, y_pred_rf)

# Retornar a importância das variáveis, MSE e R²
rf_feature_importances = random_forest_model.feature_importances_
print("MSE:", mse_rf, "\nR2: ", r2_rf, "\nFeatures Importance: ", rf_feature_importances)

MSE: 1.3184383147355705 
R2:  0.9985239293827841 
Features Importance:  [2.97453666e-04 3.14328555e-04 3.45187058e-05 5.03547968e-05
 2.35441889e-01 6.03102796e-01 5.09939041e-02 1.09764756e-01]


# Ciclista_mortes

In [68]:
#calculo da correlação para variável de interesse

# A variável alvo
variavel_alvo = 'Ciclista_mortes'

# Criar um DataFrame para armazenar as correlações
correlacoes = pd.Series(dtype=float)

# Calcular a correlação para cada coluna com a variável alvo
for coluna in df_encoded.columns:
    if coluna != variavel_alvo:  # Evitar a correlação da variável com ela mesma
        correlacao = np.corrcoef(df_encoded[variavel_alvo], df_encoded[coluna])[0, 1]
        correlacoes[coluna] = correlacao
        

# Selecionar os 10 maiores valores negativos e os 10 maiores valores positivos
maiores_positivos = correlacoes.sort_values(ascending=False).head(10)
maiores_negativos = correlacoes.sort_values(ascending=True).head(10)

# Exibir os resultados
print("Maiores correlações negativas:")
print(maiores_negativos)
print("\nMaiores correlações positivas:")
print(maiores_positivos)

Maiores correlações negativas:
origem_NPAC_DBGESTORES                                         -0.280627
dsc_unidade_SEMOB                                              -0.223774
dsc_fonte_OGU                                                  -0.193421
situacao_obra_OBJETO CONCLUÍDO                                 -0.093551
Categoria_emprendimentos_Pavimentação, Drenagem e Saneamento   -0.081714
dias_paralisados                                               -0.078688
dsc_situacao_contrato_mdr_CONTRATADO - CONCLUIDO               -0.048476
uf_SIGLA_UF_x_BA                                               -0.039670
uf_SIGLA_UF_x_RS                                               -0.038477
uf_SIGLA_UF_x_MG                                               -0.035744
dtype: float64

Maiores correlações positivas:
Motociclista_mortes               0.867256
total_mortes                      0.834841
Ocup_automovel_mortes             0.777461
Pedestre_mortes                   0.739827
total_feridos       

In [70]:
# Selecionar variáveis relevantes para prever mortes de ciclistas
features = ['origem_NPAC_DBGESTORES', 'dsc_unidade_SEMOB','dsc_fonte_OGU','situacao_obra_OBJETO CONCLUÍDO',
            'Motociclista_mortes','Ocup_automovel_mortes','Pedestre_mortes','total_feridos']
target = 'Ciclista_mortes'

# Criar os conjuntos de treino e teste
X = df_encoded[features]
y = df_encoded[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [71]:
# Configurar e treinar o modelo de regressão linear
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred = linear_model.predict(X_test)

# Avaliar a performance do modelo
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("MSE:", mse, "R2:", r2)

MSE: 2.286182930612516 R2: 0.7632461911863193


In [72]:
from sklearn.ensemble import RandomForestRegressor

# Configurar e treinar o modelo Random Forest
random_forest_model = RandomForestRegressor(n_estimators=100, random_state=42)
random_forest_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred_rf = random_forest_model.predict(X_test)

# Avaliar a performance do modelo
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2_rf = r2_score(y_test, y_pred_rf)

# Retornar a importância das variáveis, MSE e R²
rf_feature_importances = random_forest_model.feature_importances_
print("MSE:", mse_rf, "\nR2: ", r2_rf, "\nFeatures Importance: ", rf_feature_importances)

MSE: 0.10441500741460126 
R2:  0.9891869323439956 
Features Importance:  [1.42907346e-04 2.08828757e-05 9.13868956e-05 2.96633059e-04
 6.86874987e-01 1.09988390e-01 1.45903242e-01 5.66815704e-02]


# Ocup_automovel_mortes  

In [73]:
#calculo da correlação para variável de interesse

# A variável alvo
variavel_alvo = 'Ocup_automovel_mortes'

# Criar um DataFrame para armazenar as correlações
correlacoes = pd.Series(dtype=float)

# Calcular a correlação para cada coluna com a variável alvo
for coluna in df_encoded.columns:
    if coluna != variavel_alvo:  # Evitar a correlação da variável com ela mesma
        correlacao = np.corrcoef(df_encoded[variavel_alvo], df_encoded[coluna])[0, 1]
        correlacoes[coluna] = correlacao
        

# Selecionar os 10 maiores valores negativos e os 10 maiores valores positivos
maiores_positivos = correlacoes.sort_values(ascending=False).head(10)
maiores_negativos = correlacoes.sort_values(ascending=True).head(10)

# Exibir os resultados
print("Maiores correlações negativas:")
print(maiores_negativos)
print("\nMaiores correlações positivas:")
print(maiores_positivos)

Maiores correlações negativas:
origem_NPAC_DBGESTORES                                         -0.300844
dsc_unidade_SEMOB                                              -0.253561
dsc_fonte_OGU                                                  -0.216122
situacao_obra_OBJETO CONCLUÍDO                                 -0.108494
dias_paralisados                                               -0.093059
Categoria_emprendimentos_Pavimentação, Drenagem e Saneamento   -0.088042
dsc_situacao_contrato_mdr_CONTRATADO - CONCLUIDO               -0.057082
uf_SIGLA_UF_x_RS                                               -0.041619
uf_SIGLA_UF_x_RN                                               -0.039103
uf_SIGLA_UF_x_PI                                               -0.037834
dtype: float64

Maiores correlações positivas:
total_mortes                      0.870684
Motociclista_mortes               0.820593
Pedestre_mortes                   0.811130
Ciclista_mortes                   0.777461
total_feridos       

In [74]:
# Selecionar variáveis relevantes para prever mortes em veículos
features = ['origem_NPAC_DBGESTORES', 'dsc_unidade_SEMOB','dsc_fonte_OGU','dias_paralisados',
            'Motociclista_mortes','Pedestre_mortes','Ciclista_mortes','Ocup_automovel_feridos']
target = 'Ocup_automovel_mortes'

# Criar os conjuntos de treino e teste
X = df_encoded[features]
y = df_encoded[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [75]:
# Configurar e treinar o modelo de regressão linear
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred = linear_model.predict(X_test)

# Avaliar a performance do modelo
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("MSE:", mse, "R2:", r2)

MSE: 30.845316679074315 R2: 0.7696191208503942


In [76]:
from sklearn.ensemble import RandomForestRegressor

# Configurar e treinar o modelo Random Forest
random_forest_model = RandomForestRegressor(n_estimators=100, random_state=42)
random_forest_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred_rf = random_forest_model.predict(X_test)

# Avaliar a performance do modelo
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2_rf = r2_score(y_test, y_pred_rf)

# Retornar a importância das variáveis, MSE e R²
rf_feature_importances = random_forest_model.feature_importances_
print("MSE:", mse_rf, "\nR2: ", r2_rf, "\nFeatures Importance: ", rf_feature_importances)

MSE: 4.165572015687606 
R2:  0.9688877195484865 
Features Importance:  [2.40571182e-04 4.50258889e-05 2.30664462e-04 1.55952589e-02
 4.82963296e-01 3.18401184e-01 8.61309936e-02 9.63930060e-02]


- Se não considerar variáveis de mortes como variáveis independentes, ainda assim é possível criar bons modelos de previsão
- Neste caso é necessário utilizar um modelo ensamble learning, pois o nível de predição de um modelo mais simples (regressão múltipla), não será o suficiente, por conta que os dados estão fracamente correlacionados
- Exemplos estão apresentados abaixo: 

In [77]:
# Selecionar variáveis relevantes para prever mortes em veículos
features = ['origem_NPAC_DBGESTORES', 'dsc_unidade_SEMOB','dsc_fonte_OGU','dias_paralisados',
            'Ocup_automovel_feridos','Motociclista_feridos','Motociclista_feridos']
target = 'Ocup_automovel_mortes'

# Criar os conjuntos de treino e teste
X = df_encoded[features]
y = df_encoded[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [78]:
# Configurar e treinar o modelo de regressão linear
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred = linear_model.predict(X_test)

# Avaliar a performance do modelo
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print("MSE:", mse, "R2:", r2)

MSE: 55.3531161411044 R2: 0.5865725843265821


In [79]:
from sklearn.ensemble import RandomForestRegressor

# Configurar e treinar o modelo Random Forest
random_forest_model = RandomForestRegressor(n_estimators=100, random_state=42)
random_forest_model.fit(X_train, y_train)

# Fazer previsões com o conjunto de teste
y_pred_rf = random_forest_model.predict(X_test)

# Avaliar a performance do modelo
mse_rf = mean_squared_error(y_test, y_pred_rf)
r2_rf = r2_score(y_test, y_pred_rf)

# Retornar a importância das variáveis, MSE e R²
rf_feature_importances = random_forest_model.feature_importances_
print("MSE:", mse_rf, "\nR2: ", r2_rf, "\nFeatures Importance: ", rf_feature_importances)

MSE: 10.796768436656532 
R2:  0.9193599135229792 
Features Importance:  [3.92293176e-03 4.81906992e-04 5.59430459e-04 2.49027100e-02
 6.22403800e-01 1.68745482e-01 1.78983738e-01]
